In [1]:
import numpy as np
import pandas as pd

file_path = "../../data/raw/yp_competitors_rws.csv"
file_path = "../../data/processed/yp_kimos-maui-lahaina_rws.csv"
df = pd.read_csv(file_path) 

In [2]:
## imports
from itertools import chain
from nltk import word_tokenize, sent_tokenize, pos_tag
from nltk import FreqDist
from nltk import WordNetLemmatizer, PorterStemmer
from nltk.corpus import stopwords
import matplotlib.pyplot as plt

In [3]:
df.head()

status                                            reviews
0       1  Kimo's never disappoints.  We come here once o...
1       0  I was there the first week of October and Firs...
2       1  This place was on my "Must Do Maui" list and i...
3       0  Monday night dinner here and they quickly sat ...
4       1  Nice view and amazing cocktails. They are loca...

## Tokenization

In [4]:
df['sent_tokens'] = df.reviews.apply(lambda x: sent_tokenize(x))

In [5]:
df['word_tokens'] = df.sent_tokens.apply(
    lambda x: [w
               for s in x
               for w in word_tokenize(s) if w.isalpha()]
)

In [6]:
df['pos_tag'] = df.word_tokens.apply(lambda x: pos_tag(x))

In [12]:
print(df.loc[0, ['sent_tokens', 'word_tokens']].sent_tokens)
print()
print(df.loc[0, ['sent_tokens', 'word_tokens']].word_tokens)

["Kimo's never disappoints.", 'We come here once on every trip we make to Maui, and it is always consistently great service and food.', 'We sat upstairs this time, and had a beautiful ocean view.', 'I love that they bring out fresh carrot muffins while you wait for your food, the kids devoured them.', 'For dinner we ordered a lobster topped red snapper and a white fish with pesto, both of which were delicious.', 'The kids enjoyed their meals off the kids menu as well.', 'I definitely recommend making reservations as it gets pretty packed around dinner time.', 'We were seated right away since we made a reservation- but I saw a lot of people waiting who did not make one.']

['Kimo', 'never', 'disappoints', 'We', 'come', 'here', 'once', 'on', 'every', 'trip', 'we', 'make', 'to', 'Maui', 'and', 'it', 'is', 'always', 'consistently', 'great', 'service', 'and', 'food', 'We', 'sat', 'upstairs', 'this', 'time', 'and', 'had', 'a', 'beautiful', 'ocean', 'view', 'I', 'love', 'that', 'they', 'bring

In [17]:
len(chain(*df.sent_tokens.iloc[:5]))

TypeError: object of type 'itertools.chain' has no len()

## Stopwords

In [13]:
tokens = chain(*df.word_tokens)
tokens = [w for w in tokens if w.lower() not in stopwords.words('english')]

In [14]:
len(tokens)

113970

## Vocabulary
- lowercased
- punctuation removed
- stopwords removed

In [15]:
vocab = sorted(set(w.lower() for w in tokens))
tokens_freq = FreqDist(w.lower() for w in tokens)

In [16]:
len(vocab)

7239

In [17]:
len(tokens_freq)

7239

In [18]:
# lexicality score
len(vocab) / len(tokens) 

0.06351671492498026

In [19]:
print(tokens_freq.most_common(20))

[('great', 1716), ('food', 1680), ('good', 1649), ('fish', 1531), ('service', 1105), ('view', 1056), ('kimo', 968), ('pie', 936), ('hula', 867), ('place', 860), ('maui', 793), ('dinner', 746), ('us', 686), ('would', 646), ('ordered', 603), ('get', 599), ('really', 593), ('one', 581), ('time', 575), ('back', 573)]


## Normalization

In [20]:
lemmatizer = WordNetLemmatizer()
porter = PorterStemmer()
vocab2 = [porter.stem(lemmatizer.lemmatize(w)) for i, w in enumerate(vocab)]
# vocab2 = [lemmatizer.lemmatize(porter.stem(w)) for i, w in enumerate(vocab)]

In [21]:
vocab2_freq = FreqDist(vocab2)

In [22]:
len(vocab2)

7239

In [23]:
len(vocab2_freq)

5226

In [24]:
print(vocab2_freq.most_common(20))

[('manag', 8), ('consist', 7), ('season', 7), ('care', 6), ('celebr', 6), ('enjoy', 6), ('indulg', 6), ('person', 6), ('prepar', 6), ('recommend', 6), ('review', 6), ('select', 6), ('suggest', 6), ('travel', 6), ('arriv', 5), ('compar', 5), ('compens', 5), ('disappoint', 5), ('except', 5), ('expect', 5)]


## Apply to each document in corpora

In [25]:
df['norm_tokens'] = df.word_tokens.apply(
    lambda x: [porter.stem(lemmatizer.lemmatize(w.lower()))
                                  for w in x if w.lower() not in stopwords.words('english')]
)

In [26]:
df.head()

status                                            reviews  \
0       1  Kimo's never disappoints.  We come here once o...   
1       0  I was there the first week of October and Firs...   
2       1  This place was on my "Must Do Maui" list and i...   
3       0  Monday night dinner here and they quickly sat ...   
4       1  Nice view and amazing cocktails. They are loca...   

                                         sent_tokens  \
0  [Kimo's never disappoints., We come here once ...   
1  [I was there the first week of October and Fir...   
2  [This place was on my "Must Do Maui" list and ...   
3  [Monday night dinner here and they quickly sat...   
4  [Nice view and amazing cocktails., They are lo...   

                                         word_tokens  \
0  [Kimo, never, disappoints, We, come, here, onc...   
1  [I, was, there, the, first, week, of, October,...   
2  [This, place, was, on, my, Must, Do, Maui, lis...   
3  [Monday, night, dinner, here, and, they, quick...   
4  [Nice, view, and, amazing, cocktails, They, ar...   

                                             pos_tag  \
0  [(Kimo, NNP), (never, RB), (disappoints, VBZ),...   
1  [(I, PRP), (was, VBD), (there, RB), (the, DT),...   
2  [(This, DT), (place, NN), (was, VBD), (on, IN)...   
3  [(Monday, NNP), (night, NN), (dinner, NN), (he...   
4  [(Nice, NNP), (view, NN), (and, CC), (amazing,...   

                                         norm_tokens  
0  [kimo, never, disappoint, come, everi, trip, m...  
1  [first, week, octob, first, think, staff, wond...  
2  [place, must, maui, list, disappoint, must, co...  
3  [monday, night, dinner, quickli, sat, group, u...  
4  [nice, view, amaz, cocktail, locat, right, lah...

In [27]:
df.to_csv('../../data/processed/yp_kimos-maui-lahaina_rws_preprocessed.csv', index=False)

In [29]:
df.apply(lambda x: x.reviews, axis=1).head()

0    Kimo's never disappoints.  We come here once o...
1    I was there the first week of October and Firs...
2    This place was on my "Must Do Maui" list and i...
3    Monday night dinner here and they quickly sat ...
4    Nice view and amazing cocktails. They are loca...
dtype: object

In [33]:
print([1 if w in vocab else 0 for w in df.norm_tokens[0]])

[1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1]


In [34]:
print(df.norm_tokens[0])

['kimo', 'never', 'disappoint', 'come', 'everi', 'trip', 'make', 'maui', 'alway', 'consist', 'great', 'servic', 'food', 'sat', 'upstair', 'time', 'beauti', 'ocean', 'view', 'love', 'bring', 'fresh', 'carrot', 'muffin', 'wait', 'food', 'kid', 'devour', 'dinner', 'order', 'lobster', 'top', 'red', 'snapper', 'white', 'fish', 'pesto', 'delici', 'kid', 'enjoy', 'meal', 'kid', 'menu', 'well', 'definit', 'recommend', 'make', 'reserv', 'get', 'pretti', 'pack', 'around', 'dinner', 'time', 'seat', 'right', 'away', 'sinc', 'made', 'saw', 'lot', 'peopl', 'wait', 'make', 'one']


## classifier test

In [35]:
import nltk
from nltk.corpus import movie_reviews
import random
df.head()

documents = df.loc[:, ['norm_tokens', 'status']].values

random.shuffle(documents)

In [36]:
word_features = list(vocab2_freq)#[:2000]

In [37]:
def document_features(document):
    document_words = set(document)
    features = {}
    for word in word_features:
        features['contains({})'.format(word)] = (word in document_words)
    return features

In [38]:
# Train Naive Bayes classifier
featuresets = [(document_features(d), c) for (d,c) in documents]
train_set, test_set = featuresets[100:], featuresets[:100]
classifier = nltk.NaiveBayesClassifier.train(train_set)

In [39]:
# Test the classifier
print(nltk.classify.accuracy(classifier, test_set))

0.95


In [40]:
# Show the most important features as interpreted by Naive Bayes
classifier.show_most_informative_features(10)

Most Informative Features
          contains(rude) = True                0 : 1      =     63.7 : 1.0
         contains(speak) = True                0 : 1      =     35.9 : 1.0
        contains(apolog) = True                0 : 1      =     29.0 : 1.0
         contains(settl) = True                0 : 1      =     26.7 : 1.0
         contains(overr) = True                0 : 1      =     22.9 : 1.0
        contains(explan) = True                0 : 1      =     22.0 : 1.0
         contains(desir) = True                0 : 1      =     22.0 : 1.0
            contains(aw) = True                0 : 1      =     19.7 : 1.0
         contains(chili) = True                0 : 1      =     19.7 : 1.0
      contains(distract) = True                0 : 1      =     19.7 : 1.0


In [46]:
test_set

[({'contains(aaa)': False,
   'contains(abc)': False,
   'contains(abhor)': False,
   'contains(abi)': False,
   'contains(abid)': False,
   'contains(abil)': False,
   'contains(abl)': False,
   'contains(abnorm)': False,
   'contains(abound)': False,
   'contains(abruptli)': False,
   'contains(absenc)': False,
   'contains(absent)': False,
   'contains(absolut)': False,
   'contains(absurd)': False,
   'contains(abund)': False,
   'contains(ac)': False,
   'contains(accent)': False,
   'contains(accept)': False,
   'contains(access)': False,
   'contains(accid)': False,
   'contains(accident)': False,
   'contains(acclaim)': False,
   'contains(accommod)': False,
   'contains(accomod)': False,
   'contains(accompani)': False,
   'contains(accompli)': False,
   'contains(accomplish)': False,
   'contains(accord)': False,
   'contains(accordingli)': False,
   'contains(accuraci)': False,
   'contains(accur)': False,
   'contains(accustom)': False,
   'contains(achiev)': False,
   'con